# Blocking with Word2Vec

In [1]:
from gensim.models import Word2Vec
from gensim.utils import simple_preprocess
from sklearn.cluster import KMeans
import numpy as np
import pandas as pd
import os
import gensim.downloader as api
from sklearn.metrics import silhouette_score
import csv

In [2]:
import os

num_threads = os.cpu_count()
print("Numero di thread disponibili:", num_threads)

Numero di thread disponibili: 8


In [3]:
schema_mediato = pd.read_csv("./../../datasets/MediatedSchemaSemicolon.csv",sep=";")

In [30]:
schema_mediato

name                         location        marketCap sharePrice  \
0       Lacework          United States, San Jose            $8.3B        NaN   
1        Tipalti         United States, San Mateo            $8.3B        NaN   
2         Tempus           United States, Chicago            $8.1B        NaN   
3        Anduril            United States, Irvine           $8.48B        NaN   
4           Bolt                 Estonia, Tallinn            $8.4B        NaN   
...          ...                              ...              ...        ...   
81701    PepsiCo      Purchase, NY, United States  $241.05 Billion        NaN   
81702     Costco      Issaquah, WA, United States  $258.15 Billion        NaN   
81703   Broadcom      San Jose, CA, United States  $265.27 Billion        NaN   
81704  Coca-Cola       Atlanta, GA, United States  $273.20 Billion        NaN   
81705      Lilly  Indianapolis, IN, United States  $273.01 Billion        NaN   

                      category foundationYear  
0                Cybersecurity           2015  
1                      Fintech           2010  
2                       Health           2015  
3      Artificial intelligence           2017  
4        Auto & transportation           2013  
...                        ...            ...  
81701                      NaN            NaN  
81702                      NaN            NaN  
81703                      NaN            NaN  
81704                      NaN            NaN  
81705                      NaN            NaN  

[81706 rows x 6 columns]

In [5]:
records = []

In [6]:
for i in range(0,len(schema_mediato)):
    record = schema_mediato.iloc[i].dropna()
    records.append(record.tolist())

In [7]:
records

[['Lacework', 'United States, San Jose', '$8.3B', 'Cybersecurity', '2015'],
 ['Tipalti', 'United States, San Mateo', '$8.3B', 'Fintech', '2010'],
 ['Tempus', 'United States, Chicago', '$8.1B', 'Health', '2015'],
 ['Anduril',
  'United States, Irvine',
  '$8.48B',
  'Artificial intelligence',
  '2017'],
 ['Bolt', 'Estonia, Tallinn', '$8.4B', 'Auto & transportation', '2013'],
 ['ByteDance', 'China, Beijing', '$140B', 'Artificial intelligence', '2012'],
 ['Niantic',
  'United States, San Francisco',
  '$9B',
  'Mobile & telecommunications',
  '2015'],
 ['OYO Rooms', 'India, Gurugram', '$9B', 'Travel', '2012'],
 ['Kavak',
  'Mexico, Lerma de Villada',
  '$8.7B',
  'E-commerce & direct-to-consumer',
  '2014'],
 ['Personio',
  'Germany, Munich',
  '$8.5B',
  'Internet software & services',
  '2015'],
 ['Klaviyo',
  'United States, Boston',
  '$9.2B',
  'Internet software & services',
  '2012'],
 ['Rapyd', 'United Kingdom, London', '$8.75B', 'Fintech', '2016'],
 ['Nuro',
  'United States, Mou

In [8]:
model = Word2Vec(sentences=records, vector_size=256, window=5, min_count=1, workers=4)

In [9]:
def calculate_vector(record):
    # Inizializza un vettore vuoto
    record_vector = np.zeros(model.vector_size)
    # Somma i vettori di embedding di ciascun token nel record
    for token in record:
        record_vector += model.wv[token]
    #Normalizza il vettore risultante
    record_vector /= 100
    return record_vector

In [11]:
records_w2v = []
for i in range(0, len(records)):
    records_w2v.append(calculate_vector(records[i]))

In [12]:
records_w2v

[array([ 4.20779619e-03, -6.45275903e-03, -3.40566540e-03,  3.40225987e-03,
         8.20703661e-03,  3.83412933e-04,  3.56791961e-03,  7.13151661e-04,
        -4.64040536e-03,  5.73940540e-03,  9.55101557e-04, -4.57259024e-03,
         1.87272306e-04, -4.06874927e-03, -5.30696237e-03,  2.18335609e-03,
         3.17229084e-03, -4.30695068e-03, -1.07865950e-02,  1.32090025e-02,
         4.86015440e-03,  5.41149302e-03, -1.86446560e-03, -1.09573966e-02,
        -4.13779129e-03,  3.94662090e-03,  4.85420056e-03, -3.68978453e-03,
         1.88059371e-03, -8.30124213e-03, -1.34846131e-03,  3.80791684e-03,
        -1.45943644e-03, -1.62456462e-03, -2.47129405e-03,  2.64839667e-03,
         6.54758919e-03, -4.85459051e-03, -2.34833648e-03, -4.22868462e-03,
        -4.70824154e-03,  6.42696396e-03, -4.14212919e-03,  3.82123567e-03,
         9.18097978e-03, -1.10015986e-03, -8.76968028e-06,  8.46042000e-04,
        -4.15678515e-03, -9.40539594e-04, -9.06202353e-04,  1.95056844e-03,
         2.7

In [13]:
df = pd.DataFrame(records_w2v)
df

0         1         2         3         4         5         6    \
0      0.004208 -0.006453 -0.003406  0.003402  0.008207  0.000383  0.003568   
1      0.007296 -0.009081 -0.003975  0.004768  0.011376  0.001278  0.004529   
2      0.004548 -0.007321 -0.004254  0.003662  0.009359  0.000574  0.003994   
3      0.004070 -0.005223 -0.002551  0.002866  0.006735  0.000610  0.002838   
4      0.003749 -0.005557 -0.002632  0.003041  0.006771  0.000268  0.003036   
...         ...       ...       ...       ...       ...       ...       ...   
81701  0.000366 -0.000381  0.000007  0.000199  0.000358  0.000043  0.000157   
81702  0.000329 -0.000303 -0.000040  0.000173  0.000316  0.000099  0.000128   
81703  0.001143 -0.001065 -0.000175  0.000689  0.001214  0.000102  0.000451   
81704  0.001059 -0.001000 -0.000102  0.000717  0.001151  0.000098  0.000451   
81705  0.000151 -0.000133 -0.000057  0.000110  0.000216  0.000052  0.000064   

            7         8         9    ...       246       247       248  \
0      0.000713 -0.004640  0.005739  ...  0.001583  0.004071  0.003248   
1      0.001274 -0.005578  0.006326  ...  0.003534  0.005787  0.003851   
2      0.000639 -0.005783  0.007120  ...  0.001034  0.004537  0.004107   
3      0.000687 -0.003339  0.003907  ...  0.001860  0.003286  0.002400   
4      0.000616 -0.003773  0.004633  ...  0.001377  0.003381  0.002614   
...         ...       ...       ...  ...       ...       ...       ...   
81701  0.000107 -0.000101  0.000069  ...  0.000352  0.000196  0.000087   
81702  0.000118 -0.000031  0.000132  ...  0.000264  0.000201 -0.000031   
81703  0.000254 -0.000184  0.000132  ...  0.000858  0.000677  0.000149   
81704  0.000209 -0.000261  0.000193  ...  0.000835  0.000645  0.000101   
81705  0.000095 -0.000072 -0.000063  ...  0.000133  0.000094  0.000022   

            249       250       251       252       253       254       255  
0     -0.004637 -0.005286  0.000106 -0.007883  0.005752 -0.007746  0.001335  
1     -0.006094 -0.006670 -0.000356 -0.010126  0.007216 -0.010132  0.001827  
2     -0.005633 -0.006508  0.000146 -0.009699  0.007227 -0.009033  0.001756  
3     -0.003610 -0.004024  0.000020 -0.006126  0.004459 -0.005791  0.001142  
4     -0.003858 -0.004451  0.000210 -0.006632  0.004677 -0.006497  0.000920  
...         ...       ...       ...       ...       ...       ...       ...  
81701 -0.000177 -0.000172 -0.000051 -0.000229  0.000127 -0.000248  0.000081  
81702 -0.000103 -0.000136 -0.000017 -0.000145  0.000153 -0.000239  0.000055  
81703 -0.000373 -0.000488 -0.000132 -0.000664  0.000334 -0.000921  0.000096  
81704 -0.000471 -0.000405 -0.000098 -0.000617  0.000309 -0.000864  0.000099  
81705 -0.000034 -0.000034 -0.000035 -0.000129  0.000134 -0.000044  0.000017  

[81706 rows x 256 columns]

## K Means

In [14]:
kmeans = KMeans(n_clusters=800, random_state=0).fit(df)

/Users/alessandropesare/anaconda3/envs/FinalProjectIDD3_8/lib/python3.8/site-packages/sklearn/cluster/_kmeans.py:1416: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  super()._check_params_vs_input(X, default_n_init=10)


In [15]:
len(kmeans.labels_)

81706

In [17]:
silhouette_score(df,kmeans.labels_)

0.31230233316004513

In [39]:
from itertools import islice

In [40]:

#Esegui il blocking basato sui cluster ottenuti
blocks = {}  # Dizionario che mappa il cluster al suo insieme di record
for i, label in enumerate(kmeans.labels_):
    if label not in blocks:
        blocks[label] = []
    blocks[label].append(records[i])

print("Blocchi ottenuti:")
print(len(blocks))
# Stampare i primi 100 elementi del dizionario
for key, value in islice(blocks.items(), 100):
    print(key, value)

Blocchi ottenuti:
800
403 [['Lacework', 'United States, San Jose', '$8.3B', 'Cybersecurity', '2015'], ['Nuro', 'United States, Mountain View', '$8.6B', 'Auto & transportation', '2016'], ['Lalamove', 'Hong Kong, Cheung Sha Wan', '$10B', 'Supply chain, logistics, & delivery', '2013'], ['Leap Motor', 'China, Hangzhou', '$1.01B', 'Auto & transportation', '2015'], ['Rivigo', 'India, Gurgaon', '$1.07B', 'Supply chain, logistics, & delivery', '2014'], ['LEAD School', 'India, Andheri', '$1.1B', 'Edtech', '2012'], ['Flexe', 'United States, Seattle', ' $1B', 'Supply chain, logistics, & delivery', '2013'], ['TravelPerk', 'Spain, Barcelona', '$1.3B', 'Travel', '2015'], ['Tongdun Technology', 'China, Hangzhou', '$1.32B', 'Cybersecurity', '2013'], ['Degreed', 'United States, Pleasanton', '$1.4B', 'Edtech', '2012'], ['Fresh Life Style Supply Chain Management', 'China, Chengdu', ' $1.57 B', 'Supply chain, logistics, & delivery', '2016'], ['Ximalaya FM', 'China, Shanghai', '$1.52B', 'Mobile & telecommu

In [44]:
blocks[403]

[['Lacework', 'United States, San Jose', '$8.3B', 'Cybersecurity', '2015'],
 ['Nuro',
  'United States, Mountain View',
  '$8.6B',
  'Auto & transportation',
  '2016'],
 ['Lalamove',
  'Hong Kong, Cheung Sha Wan',
  '$10B',
  'Supply chain, logistics, & delivery',
  '2013'],
 ['Leap Motor', 'China, Hangzhou', '$1.01B', 'Auto & transportation', '2015'],
 ['Rivigo',
  'India, Gurgaon',
  '$1.07B',
  'Supply chain, logistics, & delivery',
  '2014'],
 ['LEAD School', 'India, Andheri', '$1.1B', 'Edtech', '2012'],
 ['Flexe',
  'United States, Seattle',
  ' $1B',
  'Supply chain, logistics, & delivery',
  '2013'],
 ['TravelPerk', 'Spain, Barcelona', '$1.3B', 'Travel', '2015'],
 ['Tongdun Technology', 'China, Hangzhou', '$1.32B', 'Cybersecurity', '2013'],
 ['Degreed', 'United States, Pleasanton', '$1.4B', 'Edtech', '2012'],
 ['Fresh Life Style Supply Chain Management',
  'China, Chengdu',
  ' $1.57 B',
  'Supply chain, logistics, & delivery',
  '2016'],
 ['Ximalaya FM',
  'China, Shanghai',
  

## Preparazione per Record Linkage

In [45]:
schema_con_cluster = schema_mediato.copy()
schema_con_cluster['cluster'] = kmeans.labels_

In [46]:
schema_con_cluster

name                         location        marketCap sharePrice  \
0       Lacework          United States, San Jose            $8.3B        NaN   
1        Tipalti         United States, San Mateo            $8.3B        NaN   
2         Tempus           United States, Chicago            $8.1B        NaN   
3        Anduril            United States, Irvine           $8.48B        NaN   
4           Bolt                 Estonia, Tallinn            $8.4B        NaN   
...          ...                              ...              ...        ...   
81701    PepsiCo      Purchase, NY, United States  $241.05 Billion        NaN   
81702     Costco      Issaquah, WA, United States  $258.15 Billion        NaN   
81703   Broadcom      San Jose, CA, United States  $265.27 Billion        NaN   
81704  Coca-Cola       Atlanta, GA, United States  $273.20 Billion        NaN   
81705      Lilly  Indianapolis, IN, United States  $273.01 Billion        NaN   

                      category foundationYear  cluster  
0                Cybersecurity           2015      403  
1                      Fintech           2010      610  
2                       Health           2015      687  
3      Artificial intelligence           2017      372  
4        Auto & transportation           2013      372  
...                        ...            ...      ...  
81701                      NaN            NaN      328  
81702                      NaN            NaN      328  
81703                      NaN            NaN      678  
81704                      NaN            NaN      678  
81705                      NaN            NaN        8  

[81706 rows x 7 columns]

In [47]:
schema_con_cluster.to_csv("SchemaMediatoConCluster.csv")

## Esempio per un solo cluster

In [23]:
cluster5 = schema_con_cluster[schema_con_cluster['cluster'] == 5]
cluster5

name  \
10123                       ValueLabs   
10172                      Tata Elxsi   
10331      Sysnet Global Technologies   
10592  Barclays Global Service Centre   
10843  SoftAge Information Technology   
11220    PrimEra Medical Technologies   
11322     National Informatics Centre   
11344                       Suma Soft   
11556                          Sasken   
11568                IIC Technologies   
11811                    SG Analytics   
11962         Ensure Support Services   
12039                          RedBus   
12893              Bharat IT Services   
12896             e-Centric Solutions   
13035           Uneecops Technologies   
13167             Atyati Technologies   
14080              Syscom Corporation   
14095              Syscom Corporation   
14113                 Webkul Software   
14391                    Innovatiview   
14536                     InnovationM   
14681              Tudip Technologies   
14713              Tudip Technologies   
14838                  Aapna Infotech   
16077                       Aptonline   
16336              Northcorp Software   
16817              Kommineni Infotech   
17291   MicroSpark Software Solutions   
17312   MicroSpark Software Solutions   
17826               Kanerika Software   
18082                Vritti Solutions   
18312           Wizertech Informatics   
18325           Wizertech Informatics   
18392             Indovision Services   
18531                IKF Technologies   
18577            QwikCilver Solutions   
18893            Infocus Technologies   
18896        Secure Network Solutions   
18902              AFour Technologies   
19075      Heureux Software Solutions   
19214       Vengai Software Solutions   
19268             Srijan Technologies   
19287             Srijan Technologies   
19372            Ilensys Technologies   

                                       location marketCap sharePrice  \
10123  Hyderabad/Secunderabad, Telangana, India       NaN        NaN   
10172     Bangalore/Bengaluru, Karnataka, India       NaN        NaN   
10331                   Delhi/NCR, Delhi, India       NaN        NaN   
10592                               Pune, India       NaN        NaN   
10843          Gurgaon/Gurugram, Haryana, India       NaN        NaN   
11220  Hyderabad/Secunderabad, Telangana, India       NaN        NaN   
11322                          New Delhi, India       NaN        NaN   
11344                               Pune, India       NaN        NaN   
11556     Bangalore/Bengaluru, Karnataka, India       NaN        NaN   
11568  Hyderabad/Secunderabad, Telangana, India       NaN        NaN   
11811                               Pune, India       NaN        NaN   
11962                Chennai, Tamil Nadu, India       NaN        NaN   
12039                Bangalore,Karnataka, India       NaN        NaN   
12893               Noida, Uttar Pradesh, India       NaN        NaN   
12896                          Hyderabad, India       NaN        NaN   
13035                   Delhi/NCR, Delhi, India       NaN        NaN   
13167                Bangalore,Karnataka, India       NaN        NaN   
14080               Noida, Uttar Pradesh, India       NaN        NaN   
14095               Noida, Uttar Pradesh, India       NaN        NaN   
14113               Noida, Uttar Pradesh, India       NaN        NaN   
14391               Noida, Uttar Pradesh, India       NaN        NaN   
14536               Noida, Uttar Pradesh, India       NaN        NaN   
14681                  Pune, Maharashtra, India       NaN        NaN   
14713                  Pune, Maharashtra, India       NaN        NaN   
14838               Delhi/NCR, New Delhi, India       NaN        NaN   
16077                          Hyderabad, India       NaN        NaN   
16336          Gurgaon/Gurugram, Haryana, India       NaN        NaN   
16817                          Hyderabad, India       NaN        NaN   
17291                          Hyderabad, India       NaN 

In [36]:
result = pd.merge(cluster5, cluster5, on='cluster', suffixes=('_left', '_right'))
result


name_left                             location_left  \
0                ValueLabs  Hyderabad/Secunderabad, Telangana, India   
1                ValueLabs  Hyderabad/Secunderabad, Telangana, India   
2                ValueLabs  Hyderabad/Secunderabad, Telangana, India   
3                ValueLabs  Hyderabad/Secunderabad, Telangana, India   
4                ValueLabs  Hyderabad/Secunderabad, Telangana, India   
...                    ...                                       ...   
2020  Ilensys Technologies                          Hyderabad, India   
2021  Ilensys Technologies                          Hyderabad, India   
2022  Ilensys Technologies                          Hyderabad, India   
2023  Ilensys Technologies                          Hyderabad, India   
2024  Ilensys Technologies                          Hyderabad, India   

     marketCap_left sharePrice_left             category_left  \
0               NaN             NaN  IT Services & Consulting   
1               NaN             NaN  IT Services & Consulting   
2               NaN             NaN  IT Services & Consulting   
3               NaN             NaN  IT Services & Consulting   
4               NaN             NaN  IT Services & Consulting   
...             ...             ...                       ...   
2020            NaN             NaN  IT Services & Consulting   
2021            NaN             NaN  IT Services & Consulting   
2022            NaN             NaN  IT Services & Consulting   
2023            NaN             NaN  IT Services & Consulting   
2024            NaN             NaN  IT Services & Consulting   

     foundationYear_left  cluster                      name_right  \
0                  1997         5                       ValueLabs   
1                  1997         5                      Tata Elxsi   
2                  1997         5      Sysnet Global Technologies   
3                  1997         5  Barclays Global Service Centre   
4                  1997         5  SoftAge Information Technology   
...                  ...      ...                             ...   
2020               2009         5      Heureux Software Solutions   
2021               2009         5       Vengai Software Solutions   
2022               2009         5             Srijan Technologies   
2023               2009         5             Srijan Technologies   
2024               2009         5            Ilensys Technologies   

                                location_right marketCap_right  \
0     Hyderabad/Secunderabad, Telangana, India             NaN   
1        Bangalore/Bengaluru, Karnataka, India             NaN   
2                      Delhi/NCR, Delhi, India             NaN   
3                                  Pune, India             NaN   
4             Gurgaon/Gurugram, Haryana, India             NaN   
...                                        ...             ...   
2020                   Delhi/NCR, Delhi, India             NaN   
2021                          Hyderabad, India             NaN   
2022                   Delhi/NCR, Delhi, India             NaN   
2023                   Delhi/NCR, Delhi, India             NaN   
2024                          Hyderabad, India             NaN   

     sharePrice_right            category_right foundationYear_right  
0                 NaN  IT Services & Consulting                1997   
1                 NaN  IT Services & Consulting                1989   
2                 NaN  IT Services & Consulting                1999   
3                 NaN  IT Services & Consulting                2007   
4                 NaN  IT Services & Consulting                1994   
...               ...                       ...                  ...  
2020              NaN  IT Services & Consulting                2015   
2021              NaN  IT Services & Consulting                2010   
2022              NaN  IT Services & Consulting                2002   
2023              NaN  IT Services & Co